In [1]:
%load_ext autoreload
%autoreload 2

# Exploratory Data Analysis

In [35]:
import pandas as pd
import os

from shapely.geometry import Polygon
import geopandas as gpd


import sys
sys.path.append("../")

#from src.data.loading import temp_func

# Weather Data

## Observation/climate data

### Loading the data
***Note*** that there is observation files for each day of the year (365 total files), hence these observation files will eventually need to be concatenated.

In [16]:
first_weather_obs_path = "../data/raw/weather/climate/2018/2018-01-01.txt"
weather_obs_df = pd.read_json(first_weather_obs_path, lines=True)

#expand the properties feature, add to df and remove the OG column
weather_obs_df = weather_obs_df.join(pd.json_normalize(weather_obs_df["properties"])).drop(columns=["properties"])

#basic inspection
print(weather_obs_df.shape)
weather_obs_df.head(3)

(281358, 12)


geometry  ... value
0  {'coordinates': [[[10.2463, 54.8607], [10.4021...  ...   0.0
1  {'coordinates': [[[12.1702, 55.545], [12.3284,...  ...  90.0
2  {'coordinates': [[[11.4807, 54.6619], [11.6355...  ...   0.0

[3 rows x 12 columns]

### Correcting datatypes

Start by inspecting current datatypes

In [17]:
weather_obs_df.dtypes

geometry           object
type               object
id                 object
calculatedAt       object
cellId             object
created            object
from               object
parameterId        object
qcStatus           object
timeResolution     object
to                 object
value             float64
dtype: object

Quickly checking the possible values of the `type` column as it seems redundant 

In [20]:
weather_obs_df["type"].unique()

array(['Feature'], dtype=object)

Ensuring that time related and categorical variables are casted to the correct dtypes, as well as ensuring that the geometry column is cast to an actual geometry object.

In [22]:
#create a shapely polygon from the coordinates in the geometry column
weather_obs_df["geometry"] = weather_obs_df["geometry"].apply(lambda x: Polygon(x["coordinates"][0])) # the [0] is used as list of coordinates is nested

#convert appropriate columns to datetime datatype
weather_obs_df[['calculatedAt', 'created', 'from', 'to']] = weather_obs_df[['calculatedAt', 'created', 'from', 'to']].apply(pd.to_datetime, format='mixed', utc=True)

#convert to categorical variables
weather_obs_df[["cellId", "parameterId", "qcStatus", "timeResolution"]] = weather_obs_df[["cellId", "parameterId", "qcStatus", "timeResolution"]].astype("category")


In [23]:
weather_obs_df.dtypes

geometry                       object
type                           object
id                             object
calculatedAt      datetime64[ns, UTC]
cellId                       category
created           datetime64[ns, UTC]
from              datetime64[ns, UTC]
parameterId                  category
qcStatus                     category
timeResolution               category
to                datetime64[ns, UTC]
value                         float64
dtype: object

### Extracting and visualizing grid

In [26]:
weather_obs_grid_df = weather_obs_df[['cellId', 'geometry']].drop_duplicates()
obs_grid_gdf = gpd.GeoDataFrame(weather_obs_grid_df, geometry="geometry", crs="EPSG:4326")

obs_grid_gdf.explore()

Saving the weather observation grid to a `.gpkg` file

In [ ]:
#obs_grid_gdf.to_file("temp.gpkg", layer="weather_obs_grid", driver="GPKG")

# Windmill data

## Windmill meta data

### Loading the data

In [44]:
windmill_path = "../data/raw/windmill/"
windmill_meta_path = os.path.join(windmill_path, "masterdatawind.parquet")

windmill_meta_df = pd.read_parquet(windmill_meta_path, engine="auto")
print(windmill_meta_df.shape)
windmill_meta_df.head(3)

(85150, 24)


GSRN  ...           Valid_from
0  000000000000000000  ...  2012-07-31 23:00:00
1  570714700000000027  ...                 None
2  570714700000000027  ...                 None

[3 rows x 24 columns]

### Removing unwanted rows

In [41]:
#windmill_df = windmill_df.dropna(subset=("UTM_x", "UTM_y"))
#print(windmill_df.shape)
#windmill_df.head(3)

## Windmill production data

### Loading the data

In [43]:
windmill_prod_path = "../data/raw/windmill/settlement/"
windmill_prod_2019_path = os.path.join(windmill_prod_path, "2019.parquet")


windmill_prod_2019_df = pd.read_parquet(windmill_prod_2019_path)
windmill_prod_2019_df.head(3)

GSRN  ...             TIME_CET
0  570715000000023965  ...  2019-01-27 19:00:00
1  570715000000023965  ...  2019-01-27 19:15:00
2  570715000000023965  ...  2019-01-27 19:30:00

[3 rows x 4 columns]

## Combining and visualizing meta and production data

### Finding common IDs (GSRN)

In [73]:
windmills_in_all_meta_data = windmill_meta_df.GSRN.unique()
print("Number of unique windmills in meta data:", len(windmills_in_all_meta_data))

windmills_in_2019_prod_data = windmill_prod_2019_df.GSRN.unique()
print("Number of unique windmills in 2019 production data:", len(windmills_in_2019_prod_data))


meta_data_for_windmills_with_prod_data = windmill_meta_df[windmill_meta_df.GSRN.isin(windmills_in_2019_prod_data)].drop_duplicates("GSRN")
print("Number of unique windmills where both production and meta is available:", len(meta_data_for_windmills_with_prod_data))

Number of unique windmills in meta data: 9853
Number of unique windmills in 2019 production data: 5394
Number of unique windmills where both production and meta is available: 5388


### Converting to GeoPandas

In [76]:
windmill_gdf = gpd.GeoDataFrame(
    meta_data_for_windmills_with_prod_data,
    geometry=gpd.points_from_xy(meta_data_for_windmills_with_prod_data["UTM_x"],
                                meta_data_for_windmills_with_prod_data["UTM_y"]),
    crs = "EPSG:32632"
)

windmill_gdf.explore()